In [ ]:
import numpy as np

def initialize_lists(size=30):
    initial_values = [0] * size
    return initial_values.copy(), initial_values.copy(), initial_values.copy()

def get_window(df, len_df):
    if len_df > 30:
        return df[len_df-31:len_df].astype('float32')
    else:
        return None

def transform_window(df_window, scaler):
    return scaler.transform(df_window)

def prepare_input(df_trans):
    return df_trans[:30,:].reshape((1,30,30))

def predict(model, df_new):
    return model.predict(df_new)

def calculate_residuals(df_trans, pred):
    actual = df_trans[30,:25]
    resid = actual - pred
    return actual, resid

def resize_prediction(pred, df_trans):
    pred.resize((pred.shape[0], pred.shape[1] + len(df_trans[30,25:])))
    pred[:, -len(df_trans[30,25:]):] = df_trans[30,25:]
    return pred

def inverse_transform(scaler, pred, df_trans):
    pred = scaler.inverse_transform(np.array(pred))
    actual = scaler.inverse_transform(np.array([df_trans[30,:]]))
    return actual, pred

def update_lists(actual_list, pred_list, resid_list, actual, pred, resid):
    actual_list.pop(0)
    pred_list.pop(0)
    resid_list.pop(0)
    actual_list.append(actual[0,1])
    pred_list.append(pred[0,1])
    resid_list.append(resid[0,1])
    return actual_list, pred_list, resid_list

def calculate_distances(resid, kmeans1, kmeans2, kmeans3, kmeans4):
    dist = []
    dist.append(np.linalg.norm(resid[:,1:8]-kmeans1.cluster_centers_[0], ord=2, axis=1))
    dist.append(np.linalg.norm(resid[:,8:15]-kmeans2.cluster_centers_[0], ord=2, axis=1))
    dist.append(np.linalg.norm(resid[:,15:22]-kmeans3.cluster_centers_[0], ord=2, axis=1))
    dist.append(np.linalg.norm(resid[:,22:29]-kmeans4.cluster_centers_[0], ord=2, axis=1))
    return np.array(dist)

def pipeline(df, scaler, model, kmeans1, kmeans2, kmeans3, kmeans4):
    actual_list, pred_list, resid_list = initialize_lists()
    len_df = np.len(df)
    df_window = get_window(df, len_df)
    if df_window is not None:
        df_trans = transform_window(df_window, scaler)
        df_new = prepare_input(df_trans)
        pred = predict(model, df_new)
        actual, resid = calculate_residuals(df_trans, pred)
        pred = resize_prediction(pred, df_trans)
        actual, pred = inverse_transform(scaler, pred, df_trans)
        actual_list, pred_list, resid_list = update_lists(actual_list, pred_list, resid_list, actual, pred, resid)
        dist = calculate_distances(resid, kmeans1, kmeans2, kmeans3, kmeans4)
        return actual_list, pred_list, resid_list, dist
    else:
        return actual_list, pred_list, resid_list, None


In [1]:
inp = ['a', 'b']
out = ['c','d']

inp+out

['a', 'b', 'c', 'd']